In [1]:
from huggingface_hub import notebook_login
notebook_login()

In [2]:
import pandas as pd
splits = {'Arabic': 'Data-v3.1/ARA-v3-1.csv', 'Chinese': 'Data-v3.1/ZHO-v3-1.csv', 'Czech': 'Data-v3.1/CES-v3-1.csv', 'Dutch': 'Data-v3.1/NLD-v3-1.csv', 'English': 'Data-v3.1/ENG-v3-1.csv', 'French': 'Data-v3.1/FRA-v3-1.csv', 'German': 'Data-v3.1/DEU-v3-1.csv', 'Greek': 'Data-v3.1/ELL-v3-1.csv', 'Hebrew': 'Data-v3.1/HEB-v3-1.csv', 'Hindi': 'Data-v3.1/HIN-v3-1.csv', 'Indonesian': 'Data-v3.1/IND-v3-1.csv', 'Italian': 'Data-v3.1/ITA-v3-1.csv', 'Japanese': 'Data-v3.1/JPN-v3-1.csv', 'Korean': 'Data-v3.1/KOR-v3-1.csv', 'Persian': 'Data-v3.1/PES-v3-1.csv', 'Polish': 'Data-v3.1/POL-v3-1.csv', 'Portuguese': 'Data-v3.1/POR-v3-1.csv', 'Romanian': 'Data-v3.1/RON-v3-1.csv', 'Russian': 'Data-v3.1/RUS-v3-1.csv', 'Spanish': 'Data-v3.1/SPA-v3-1.csv', 'Turkish': 'Data-v3.1/TUR-v3-1.csv', 'Vietnamese': 'Data-v3.1/VIE-v3-1.csv', 'Ukrainian': 'Data-v3.1/UKR-v3-1.csv'}
df = pd.read_csv("hf://datasets/1024m/mMGTD-Corpus/" + splits["Polish"])
df

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


ISO              LLM used       Type Data Split  \
0      POL                GPT-4o    Partial      Train   
1      POL  Amazon-Nova-Lite-1.0  Rewritten        Dev   
2      POL  Amazon-Nova-Lite-1.0    Partial       Test   
3      POL                Aya-23    Partial       Test   
4      POL    Mistral-Large-2411    Partial        Dev   
...    ...                   ...        ...        ...   
99843  POL  Amazon-Nova-Lite-1.0    Partial       Test   
99844  POL   Amazon-Nova-Pro-1.0  Rewritten       Test   
99845  POL        Gemini-Pro-1.5    Partial       Test   
99846  POL  Amazon-Nova-Lite-1.0    Partial      Train   
99847  POL  Amazon-Nova-Lite-1.0    Partial       Test   

                                           Original text  Original Word Count  \
0      Nie brak im na szczęście plusów. To na pewno w...                   29   
1      Prosto z kryminału polazłem na plebanię do ks....                   54   
2      Ryszard spotyka się profesorem w sprawie remon...                   21   
3      - Ciekawostką jest, że po jednej stronie, w wy...                   51   
4      Jeśli by się zgodził, to byłby z pewnością kro...                   43   
...                                                  ...                  ...   
99843  Dla leniwych fanów muzyki mamy dobrą informacj...                   31   
99844  Z kontroli wynika, że wojskowe zarządy infrast...                   57   
99845  Tym samym apeluję do wszystkich obywateli tego...                   59   
99846  Hurtowa cena ogórków jest niska, 'krótkie' kos...                   43   
99847  Jak zwykle, ruszając w odwiedziny do naszych C...                  113   

       Original Char Count  Split Location  \
0                      193              18   
1                      346               0   
2                      149              13   
3                      326              26   
4                      296              14   
...                    ...             ...   
99843                  202              18   
99844                  408               0   
99845                  434              29   
99846                  276              26   
99847                  768              49   

                                           Modified text  New Word Count  \
0      Nie brak im na szczęście plusów. To na pewno w...              59   
1      Dzień po wydarzeniach złożonym z plebanii księ...             113   
2      Ryszard spotyka się profesorem w sprawie remon...             107   
3      - Ciekawostką jest, że po jednej stronie, w wy...              52   
4      Jeśli by się zgodził, to byłby z pewnością kro...              69   
...                                                  ...             ...   
99843  Dla leniwych fanów muzyki mamy dobrą informacj...              74   
99844  Według ostatnich informacji, kontrola przeprow...              66   
99845  Tym samym apeluję do wszystkich obywateli tego...              99   
99846  Hurtowa cena ogórków jest niska, 'krótkie' kos...              94   
99847  Jak zwykle, ruszając w odwiedziny do naszych C...             132   

       New Char Count  
0                 397  
1                 785  
2                 732  
3                 358  
4                 458  
...               ...  
99843             512  
99844             489  
99845             733  
99846             649  
99847             939  

[99848 rows x 11 columns]

In [3]:
df = df.sample(frac=1).reset_index(drop=True)

In [4]:
df_train = df[(df['Type'].isin(['Partial', 'Rewritten', 'Unchanged'])) & (df['Data Split'] == 'Train')]
df_dev = df[(df['Type'].isin(['Partial', 'Rewritten', 'Unchanged'])) & (df['Data Split'] == 'Dev')]
df_test = df[(df['Type'].isin(['Partial', 'Rewritten', 'Unchanged'])) & (df['Data Split'] == 'Test')]
print(len(df_train))
print(len(df_dev))
print(len(df_test))

39941
9986
49921


In [5]:
POL_train = df_train.copy()
POL_dev   = df_dev.copy()
POL_test  = df_test.copy()

In [6]:
df_train['id'] = 'POL' + df_train.index.astype(str)  # Creating the 'id' column
df_train = df_train.rename(columns={'Modified text': 'text', 'Split Location': 'label'})
df_dev['id'] = 'POL' + df_dev.index.astype(str)  # Creating the 'id' column
df_dev = df_dev.rename(columns={'Modified text': 'text', 'Split Location': 'label'})
df_test['id'] = 'POL' + df_test.index.astype(str)  # Creating the 'id' column
df_test = df_test.rename(columns={'Modified text': 'text', 'Split Location': 'label'})

<ipython-input-6-80beb4d47345>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_train['id'] = 'POL' + df_train.index.astype(str)  # Creating the 'id' column
<ipython-input-6-80beb4d47345>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_dev['id'] = 'POL' + df_dev.index.astype(str)  # Creating the 'id' column
<ipython-input-6-80beb4d47345>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the cavea

In [7]:
df_train = pd.concat([df_train, df_dev], ignore_index=True)

In [8]:
print(len(df_train))
print(len(df_dev))
print(len(df_test))

49927
9986
49921


In [9]:
df_train.to_json('POL_train.jsonl', orient='records', lines=True)
df_test.to_json('POL_test.jsonl', orient='records', lines=True)

In [10]:
!pip install torch
!pip install transformers
!pip install accelerate -U
!pip install tqdm
!pip install pytorch-crf
!pip install sentencepiece

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 119.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 88.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 60.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 40.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 17.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 43.1 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalling nvidia-nvjitlink-cu12-12.5.82:
      Successfully uninstalled nvidia-nvjit

In [11]:
import os
os.makedirs("./runs/exp_seed", exist_ok=True)
os.makedirs("./runs/exp_seed/logs", exist_ok=True)
os.makedirs("./runs/exp_seed/xlmlongformerbase", exist_ok=True)

In [12]:
import torch
import json
from transformers import AutoTokenizer, AutoModelForTokenClassification
from transformers.trainer_callback import TrainerState
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence
import transformers
from torch import nn
from transformers import AutoModel, AutoConfig
from torchcrf import CRF
from torch.cuda.amp import autocast
from transformers import Trainer
from tqdm import tqdm
import numpy as np
import logging
import glob
from tqdm import tqdm
from dataclasses import dataclass, field
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger()
@dataclass
class ModelConfig:
    model_path = "hyperonym/xlm-roberta-longformer-base-16384"
    model_checkpoint_dir = "./runs"
@dataclass
class DatasetConfig:
    train_file = "/content/POL_train.jsonl"
    test_files = ["/content/POL_test.jsonl"]
@dataclass
class TrainingArgsConfig:
    do_train = False
    do_predict = False
    seed = 1024
    output_dir = "./runs/exp_seed"
    logging_steps = 160
    logging_dir = "./runs/exp_seed"
    num_train_epochs = 30
    per_device_train_batch_size = 12
    per_device_eval_batch_size = 12
    max_length = 2048
model_args = ModelConfig()
data_args = DatasetConfig()
training_args = TrainingArgsConfig()
class CRFTrainer(Trainer):
    def __init__(self, *args, **kwargs):
        super().__init__(*args, **kwargs)
    def compute_loss(self, model, inputs, return_outputs=False):
        print(inputs.keys())
        labels = inputs.pop("labels")
        outputs = model(**inputs)
        emissions = outputs[0]
        mask = inputs["attention_mask"]
        crf_loss = -model.crf(emissions, labels, mask=mask)
        return crf_loss
    def training_step(self, model, inputs):
        loss = self.compute_loss(model, inputs)
        return {"loss": loss, "inputs": inputs}
class AutoModelCRF(nn.Module):
    def __init__(self, model_name_or_path, dropout=0.075):
        super(AutoModelCRF, self).__init__()
        self.config = AutoConfig.from_pretrained(model_name_or_path)
        self.num_labels = 2
        self.encoder = AutoModel.from_pretrained(model_name_or_path, trust_remote_code=True, config=self.config, from_tf=True)
        self.dropout = nn.Dropout(dropout)
        self.linear = nn.Linear(self.config.hidden_size, self.num_labels)
        self.crf = CRF(self.num_labels, batch_first=True)
    def forward(self, input_ids, attention_mask, labels=None):
        inputs = {'input_ids': input_ids, 'attention_mask': attention_mask}
        outputs = self.encoder(**inputs)
        seq_output = outputs[0]
        seq_output = self.dropout(seq_output)
        emission = self.linear(seq_output)
        if labels is None:
            tags = self.crf.decode(emission, attention_mask.byte())
            tags_padded = []
            for idx, sequence in enumerate(tags):
                if len(attention_mask[idx]) > len(sequence):
                    tag_padded = sequence + [sequence[-1]]*(len(attention_mask[idx])-len(sequence))
                else:
                    tag_padded = sequence
                tags_padded.append(tag_padded)
            out = np.array(tags_padded)
            return out
        else:
            crf_loss = -self.crf(emission, labels, mask=attention_mask.byte())
            return crf_loss
def evaluate_position_difference(actual_position, predicted_position):
    return abs(actual_position - predicted_position)
def get_start_position(sequence, mapping=None, token_level=True):
    if mapping is not None:
        mask = mapping != -100
        sequence = sequence[mask]
        mapping = mapping[mask]
    change_indices = np.where(np.diff(sequence) == 1)[0]
    if len(change_indices) > 0:
        value = change_indices[0] + 1
    else:
        value = 0 if sequence[0] == 1 else len(sequence) - 1
    if not token_level:
        value = mapping[value] if mapping is not None else value
    return value
def evaluate_machine_start_position(labels, predictions, idx2word=None, token_level=False):
    actual_starts = []
    predicted_starts = []
    if not token_level and idx2word is None:
        raise ValueError("idx2word must be provided if evaluation is at word level (token_level=False)")
    for idx in range(labels.shape[0]):
        predict, label, mapping = (predictions[idx][1:len(labels[idx])], labels[idx][1:len(labels[idx])], idx2word[idx][1:len(labels[idx])] if not token_level else None,)
        predicted_value = get_start_position(predict, mapping, token_level)
        actual_value = get_start_position(label, mapping, token_level)
        predicted_starts.append(predicted_value)
        actual_starts.append(actual_value)
    position_differences = [ evaluate_position_difference(actual, predict) for actual, predict in zip(actual_starts, predicted_starts) ]
    mean_position_difference = np.mean(position_differences)
    return mean_position_difference
def compute_metrics(p):
    pred, labels = p
    mean_absolute_diff = evaluate_machine_start_position(labels, pred, token_level=True)
    return {"mean_absolute_diff": mean_absolute_diff,}
def training_loop(model, optimizer, train_dataloader, device):
    model.train()
    total_loss = 0
    for step, batch in enumerate(tqdm(train_dataloader)):
        input_ids = batch["input_ids"].to(device)
        attention_mask = batch["attention_mask"].to(device)
        labels = batch["labels"].to(device)
        optimizer.zero_grad()
        loss = model(input_ids, attention_mask, labels=labels)
        loss.backward()
        optimizer.step()
        logger.info(f"Step {step}: {loss.item():.4f}")
        total_loss += loss.item()
    avg_loss = total_loss/len(train_dataloader)
    print(f"Training loss: {avg_loss:.4f}")
def predict(model, test_dataloader, device):
    all_preds = []
    with torch.no_grad():
        for batch in tqdm(test_dataloader):
            input_ids = batch["input_ids"].to(device)
            attention_mask = batch["attention_mask"].to(device)
            preds = model(input_ids, attention_mask)
            all_preds.extend(preds)
    out = np.array(all_preds)
    print(out.shape)
    return out
def save_model(model_name, model, optimizer, epoch, output_dir): # train_mae, val_mae,
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
    checkpoint = {'model_state_dict': model.state_dict(),'optimizer_state_dict': optimizer.state_dict()} # 'train_mae': train_mae,'val_mae': val_mae,
    model_name = model_name.replace("/", "-")
    file_path = os.path.join(output_dir, f"{model_name}-epoch-{epoch}.pt")
    print(file_path)
    torch.save(checkpoint, file_path)
    logger.info(f"Model has been saved successfully to {file_path}")
class Semeval_Data(torch.utils.data.Dataset):
    def __init__(self, data_path, model_name, max_length=512, inference=False, debug=False):
        with open(data_path, "r") as f:
            self.data = [json.loads(line) for line in f]
        self.inference = inference
        self.tokenizer = AutoTokenizer.from_pretrained(model_name)
        self.max_length = max_length
        self.debug = debug
    def __len__(self):
        return len(self.data)
    def __getitem__(self, idx):
        text = self.data[idx]["text"]
        id = self.data[idx]["id"]
        label = None
        labels_available = "label" in self.data[idx]
        if labels_available:
            label = self.data[idx]["label"]
        labels = []
        corresponding_word = []
        tokens = []
        input_ids = []
        attention_mask = []
        for jdx, word in enumerate(text.split(" ")):
            word_encoded = self.tokenizer.tokenize(word)
            sub_words = len(word_encoded)
            if labels_available:
                is_machine_text = 1 if jdx >= label else 0
                labels.extend([is_machine_text] * sub_words)
            corresponding_word.extend([jdx] * sub_words)
            tokens.extend(word_encoded)
            input_ids.extend(self.tokenizer.convert_tokens_to_ids(word_encoded))
            attention_mask.extend([1] * sub_words)
        if len(input_ids) < self.max_length - 2:
            input_ids = ( [0] + input_ids + [2] + [1] * (self.max_length - len(input_ids) - 2) )
            if labels_available:
                labels = [0] + labels + [labels[-1]] * (self.max_length - len(labels) - 1)
            attention_mask = ( [1] + attention_mask + [1] + [0] * (self.max_length - len(attention_mask) - 2) )
            corresponding_word = ( [-100] + corresponding_word + [-100] * (self.max_length - len(corresponding_word) - 1) )
            tokens = ( [""] + tokens + [""] + [""] * (self.max_length - len(tokens) - 2) )
        else:
            input_ids = [0] + input_ids[: self.max_length - 2] + [2]
            if labels_available:
                labels = [0] + labels[: self.max_length - 2] + [labels[self.max_length - 3]]
            corresponding_word = ( [-100] + corresponding_word[: self.max_length - 2] + [-100] )
            attention_mask = [1] + attention_mask[: self.max_length - 2] + [1]
            tokens = [""] + tokens[: self.max_length - 2] + [""]
        encoded = {}
        if labels_available:
            encoded["labels"] = torch.tensor(labels)
        encoded["input_ids"] = torch.tensor(input_ids)
        encoded["attention_mask"] = torch.tensor(attention_mask)
        if labels_available:
            assert encoded["input_ids"].shape == encoded["labels"].shape
        if self.debug and not self.inference:
            encoded["partial_human_review"] = " ".join(text.split(" ")[:label])
        if self.inference:
            encoded["text"] = text
            encoded["id"] = id
            encoded["corresponding_word"] = corresponding_word
        return encoded
if __name__ == "__main__":
    model_args = ModelConfig()
    data_args = DatasetConfig()
    training_args = TrainingArgsConfig()
    transformers.set_seed(training_args.seed)
    model_path = model_args.model_path
    model_checkpoint_dir = model_args.model_checkpoint_dir
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model = AutoModelCRF(model_path).to(device)
    optimizer = torch.optim.AdamW(model.parameters(), lr=1e-5)
    train_set = Semeval_Data(data_args.train_file, model_path, max_length=training_args.max_length)
    train_dataloader = DataLoader(train_set, batch_size=training_args.per_device_train_batch_size, shuffle=True)
    train_eval_dataloader = DataLoader(train_set, batch_size=training_args.per_device_eval_batch_size, shuffle=False)
    if training_args.do_train:
        logger.info("Training...")
        logger.info("*** Train Dataset ***")
        logger.info(f"Number of samples: {len(train_set)}")
        num_train_epochs = training_args.num_train_epochs
        for epoch in tqdm(range(num_train_epochs)):
            training_loop(model, optimizer, train_dataloader, device)
            save_model(model_path, model, optimizer, epoch, model_checkpoint_dir) # ,train_mse ,val_mse

config.json:   0%|          | 0.00/772 [00:00<?, ?B/s]

tf_model.h5:   0%|          | 0.00/1.25G [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/tf_keras/src/initializers/initializers.py:121: UserWarning: The initializer TruncatedNormal is unseeded and being called multiple times, which will return identical values each time (even if the initializer is unseeded). Please update your code to provide a seed to the initializer, or avoid using the same initializer instance more than once.
  warnings.warn(
All TF 2.0 model weights were used when initializing LongformerModel.

All the weights of LongformerModel were initialized from the TF 2.0 model.
If your task is similar to the task the model of the checkpoint was trained on, you can already use LongformerModel for predictions without further training.


tokenizer_config.json:   0%|          | 0.00/453 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

In [13]:
!wget -O POL-xlm-longformer https://huggingface.co/1-800-SHARED-TASKS/POL-Checkpoints/resolve/main/POL/xlm-longformer-epoch-3.pt

--2025-02-12 00:46:16--  https://huggingface.co/1-800-SHARED-TASKS/POL-Checkpoints/resolve/main/POL/xlm-longformer-epoch-3.pt
Resolving huggingface.co (huggingface.co)... 13.35.202.121, 13.35.202.97, 13.35.202.40, ...
Connecting to huggingface.co (huggingface.co)|13.35.202.121|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.hf.co/repos/2d/ed/2ded8a949eeaac4dff2ecfae2bda1370eab45e6736628b2df88c37637e5a759d/19e002c423417efdff101333d51ec599cc8241f959d263088cc7a4fcb42e6440?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27xlm-longformer-epoch-3.pt%3B+filename%3D%22xlm-longformer-epoch-3.pt%22%3B&Expires=1739324776&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTczOTMyNDc3Nn19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmhmLmNvL3JlcG9zLzJkL2VkLzJkZWQ4YTk0OWVlYWFjNGRmZjJlY2ZhZTJiZGExMzcwZWFiNDVlNjczNjYyOGIyZGY4OGMzNzYzN2U1YTc1OWQvMTllMDAyYzQyMzQxN2VmZGZmMTAxMzMzZDUxZWM1OTljYzgyNDFmOTU5ZD

In [14]:
import os
model = AutoModelCRF(model_args.model_path).to(device)
tokenizer = AutoTokenizer.from_pretrained(model_args.model_path)
checkpoint = torch.load('POL-xlm-longformer')
model.load_state_dict(checkpoint['model_state_dict'])
model.eval()
test_sets = []
for test_file in data_args.test_files:
    test_set = Semeval_Data(test_file, model_args.model_path, max_length=training_args.max_length, inference=True)
    test_dataloader = DataLoader(test_set, batch_size=training_args.per_device_eval_batch_size, shuffle=False)
    test_sets.append(test_dataloader)
logger.info("Predicting...")
logger.info("*** Test Datasets ***")
logger.info(f"Number of sets: {len(test_sets)}")
for idx, test_set in enumerate(test_sets):
    logger.info(f"Test Dataset {idx + 1}")
    logger.info(f"Number of samples: {len(test_set)}")
    predictions = predict(model, test_set, device)
    corresponding_words = []
    ids = []
    for batch in test_set:
        corr_word_tensors = [torch.tensor(cw) for cw in batch['corresponding_word']]
        corr_word_padded = torch.nn.utils.rnn.pad_sequence(corr_word_tensors, batch_first=True, padding_value=-100)
        corr_word = np.transpose(corr_word_padded.numpy(), (1, 0))
        ids.extend(batch["id"])
        corresponding_words.extend(corr_word)
    corresponding_words = np.array(corresponding_words)
    logger.info("Predictions completed!")
    df_ids = []
    df_labels = []
    for id, pred, corr_word in zip(ids, predictions, corresponding_words):
        df_ids.append(id)
        df_labels.append(get_start_position(pred, corr_word, token_level=False))
    df = pd.DataFrame({"id": df_ids, "label": df_labels})
    file_name = os.path.basename(test_file)
    file_dirs = os.path.join(training_args.output_dir, "predictions")
    os.makedirs(file_dirs, exist_ok=True)
    file_path = os.path.join(file_dirs, file_name)
    records = df.to_dict("records")
    with open(file_path, "w") as f:
        for record in records:
            f.write(json.dumps(record) + "\n")

All TF 2.0 model weights were used when initializing LongformerModel.

All the weights of LongformerModel were initialized from the TF 2.0 model.
If your task is similar to the task the model of the checkpoint was trained on, you can already use LongformerModel for predictions without further training.
<ipython-input-14-55ce776fb81e>:4: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_global

(49921, 2048)


<ipython-input-14-55ce776fb81e>:22: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  corr_word_tensors = [torch.tensor(cw) for cw in batch['corresponding_word']]


In [15]:
!pip install jsonlines
import pandas as pd
import jsonlines
jsonl_file_path = '/content/runs/exp_seed/predictions/POL_test.jsonl'
def display_jsonl_as_dataframe(file_path):
    data = []
    with jsonlines.open(file_path) as reader:
        for obj in reader:
            data.append(obj)
    df = pd.DataFrame(data)
    return df
jsonl_df = display_jsonl_as_dataframe(jsonl_file_path)
jsonl_df

id  label
0          POL0     17
1          POL1     26
2          POL3     24
3          POL4     37
4          POL8     25
...         ...    ...
49916  POL99838     23
49917  POL99839     36
49918  POL99841     12
49919  POL99845     28
49920  POL99846     19

[49921 rows x 2 columns]

In [16]:
jsonl_file_path = '/content/POL_test.jsonl'
def display_jsonl_as_dataframe(file_path):
    data = []
    with jsonlines.open(file_path) as reader:
        for obj in reader:
            data.append(obj)
    df = pd.DataFrame(data)
    return df
jsonl_df_gold = display_jsonl_as_dataframe(jsonl_file_path)
jsonl_df_gold

ISO             LLM used     Type Data Split  \
0      POL               GPT-o1  Partial       Test   
1      POL               GPT-o1  Partial       Test   
2      POL     Gemini-Flash-1.5  Partial       Test   
3      POL               GPT-o1  Partial       Test   
4      POL    Claude-Sonnet-3.5  Partial       Test   
...    ...                  ...      ...        ...   
49916  POL  Amazon-Nova-Pro-1.0  Partial       Test   
49917  POL     Claude-Haiku-3.5  Partial       Test   
49918  POL               Aya-23  Partial       Test   
49919  POL               Aya-23  Partial       Test   
49920  POL     Claude-Haiku-3.5  Partial       Test   

                                           Original text  Original Word Count  \
0      Godne polecenia (choć paliwożerne) są turbodoł...                   41   
1      Natalia Partyka też przegrała 3:4, tyle że z K...                   52   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...                   43   
3      Opiekowała się rodzinami oficerów, którzy zgin...                   49   
4      W minionym tygodniu gminne dożynki odbyły się ...                   46   
...                                                  ...                  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...                   43   
49917  Film - który wywołał oburzenie krytyków w Cann...                   63   
49918  Pierwszy trailer gry Dead Island zrobił wielką...                   33   
49919  O ujawnienie jego treści od dawna walczą organ...                   56   
49920  75 min. - na boisku walka w środku pola, a żół...                   32   

       Original Char Count  label  \
0                      344     17   
1                      317     30   
2                      297     24   
3                      376     37   
4                      325     25   
...                    ...    ...   
49916                  311     26   
49917                  449     36   
49918                  250     17   
49919                  393     28   
49920                  192     19   

                                                    text  New Word Count  \
0      Godne polecenia ( choć paliwożerne ) są turbod...              95   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...              95   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...              58   
3      Opiekowała się rodzinami oficerów , którzy zgi...             211   
4      W minionym tygodniu gminne dożynki odbyły się ...              76   
...                                                  ...             ...   
49916  Efektownymi porównaniami rzucali też szefowie ...              91   
49917  Film - który wywołał oburzenie krytyków w Cann...              94   
49918  Pierwszy trailer gry Dead Island zrobił wielką...             143   
49919  O ujawnienie jego treści od dawna walczą organ...             109   
49920  75 min. - na boisku walka w środku pola, a żół...              77   

       New Char Count        id  
0                 705      POL0  
1                 618      POL1  
2                 404      POL3  
3                1409      POL4  
4                 566      POL8  
...               ...       ...  
49916             707  POL99838  
49917             660  POL99839  
49918            1033  POL99841  
49919             850  POL99845  
49920             478  POL99846  

[49921 rows x 12 columns]

In [17]:
jsonl_df = jsonl_df.rename(columns={'label': 'label_pred'})
jsonl_df_gold = jsonl_df_gold.rename(columns={'label': 'label_gold'})
merged_df = pd.merge(jsonl_df[['id', 'label_pred']], jsonl_df_gold[['id','text','label_gold']], on='id')
merged_df

id  label_pred  \
0          POL0          17   
1          POL1          26   
2          POL3          24   
3          POL4          37   
4          POL8          25   
...         ...         ...   
49916  POL99838          23   
49917  POL99839          36   
49918  POL99841          12   
49919  POL99845          28   
49920  POL99846          19   

                                                    text  label_gold  
0      Godne polecenia ( choć paliwożerne ) są turbod...          17  
1      Natalia Partyka też przegrała 3:4 , tyle że z ...          30  
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...          24  
3      Opiekowała się rodzinami oficerów , którzy zgi...          37  
4      W minionym tygodniu gminne dożynki odbyły się ...          25  
...                                                  ...         ...  
49916  Efektownymi porównaniami rzucali też szefowie ...          26  
49917  Film - który wywołał oburzenie krytyków w Cann...          36  
49918  Pierwszy trailer gry Dead Island zrobił wielką...          17  
49919  O ujawnienie jego treści od dawna walczą organ...          28  
49920  75 min. - na boisku walka w środku pola, a żół...          19  

[49921 rows x 4 columns]

In [18]:
merged_df['diff'] = (merged_df['label_pred'] - merged_df['label_gold']).abs()
merged_df

id  label_pred  \
0          POL0          17   
1          POL1          26   
2          POL3          24   
3          POL4          37   
4          POL8          25   
...         ...         ...   
49916  POL99838          23   
49917  POL99839          36   
49918  POL99841          12   
49919  POL99845          28   
49920  POL99846          19   

                                                    text  label_gold  diff  
0      Godne polecenia ( choć paliwożerne ) są turbod...          17     0  
1      Natalia Partyka też przegrała 3:4 , tyle że z ...          30     4  
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...          24     0  
3      Opiekowała się rodzinami oficerów , którzy zgi...          37     0  
4      W minionym tygodniu gminne dożynki odbyły się ...          25     0  
...                                                  ...         ...   ...  
49916  Efektownymi porównaniami rzucali też szefowie ...          26     3  
49917  Film - który wywołał oburzenie krytyków w Cann...          36     0  
49918  Pierwszy trailer gry Dead Island zrobił wielką...          17     5  
49919  O ujawnienie jego treści od dawna walczą organ...          28     0  
49920  75 min. - na boisku walka w środku pola, a żół...          19     0  

[49921 rows x 5 columns]

In [19]:
merged_df['id'] = merged_df['id'].str[3:].astype(int)
merged_df

id  label_pred                                               text  \
0          0          17  Godne polecenia ( choć paliwożerne ) są turbod...   
1          1          26  Natalia Partyka też przegrała 3:4 , tyle że z ...   
2          3          24  Niemcy chcieli wybudować trzy takie wjazdy, uk...   
3          4          37  Opiekowała się rodzinami oficerów , którzy zgi...   
4          8          25  W minionym tygodniu gminne dożynki odbyły się ...   
...      ...         ...                                                ...   
49916  99838          23  Efektownymi porównaniami rzucali też szefowie ...   
49917  99839          36  Film - który wywołał oburzenie krytyków w Cann...   
49918  99841          12  Pierwszy trailer gry Dead Island zrobił wielką...   
49919  99845          28  O ujawnienie jego treści od dawna walczą organ...   
49920  99846          19  75 min. - na boisku walka w środku pola, a żół...   

       label_gold  diff  
0              17     0  
1              30     4  
2              24     0  
3              37     0  
4              25     0  
...           ...   ...  
49916          26     3  
49917          36     0  
49918          17     5  
49919          28     0  
49920          19     0  

[49921 rows x 5 columns]

In [20]:
merged_df = POL_test.merge(merged_df, left_index=True, right_on='id', how='outer')
merged_df

ISO             LLM used     Type Data Split  \
0      POL               GPT-o1  Partial       Test   
1      POL               GPT-o1  Partial       Test   
2      POL     Gemini-Flash-1.5  Partial       Test   
3      POL               GPT-o1  Partial       Test   
4      POL    Claude-Sonnet-3.5  Partial       Test   
...    ...                  ...      ...        ...   
49916  POL  Amazon-Nova-Pro-1.0  Partial       Test   
49917  POL     Claude-Haiku-3.5  Partial       Test   
49918  POL               Aya-23  Partial       Test   
49919  POL               Aya-23  Partial       Test   
49920  POL     Claude-Haiku-3.5  Partial       Test   

                                           Original text  Original Word Count  \
0      Godne polecenia (choć paliwożerne) są turbodoł...                   41   
1      Natalia Partyka też przegrała 3:4, tyle że z K...                   52   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...                   43   
3      Opiekowała się rodzinami oficerów, którzy zgin...                   49   
4      W minionym tygodniu gminne dożynki odbyły się ...                   46   
...                                                  ...                  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...                   43   
49917  Film - który wywołał oburzenie krytyków w Cann...                   63   
49918  Pierwszy trailer gry Dead Island zrobił wielką...                   33   
49919  O ujawnienie jego treści od dawna walczą organ...                   56   
49920  75 min. - na boisku walka w środku pola, a żół...                   32   

       Original Char Count  Split Location  \
0                      344              17   
1                      317              30   
2                      297              24   
3                      376              37   
4                      325              25   
...                    ...             ...   
49916                  311              26   
49917                  449              36   
49918                  250              17   
49919                  393              28   
49920                  192              19   

                                           Modified text  New Word Count  \
0      Godne polecenia ( choć paliwożerne ) są turbod...              95   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...              95   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...              58   
3      Opiekowała się rodzinami oficerów , którzy zgi...             211   
4      W minionym tygodniu gminne dożynki odbyły się ...              76   
...                                                  ...             ...   
49916  Efektownymi porównaniami rzucali też szefowie ...              91   
49917  Film - który wywołał oburzenie krytyków w Cann...              94   
49918  Pierwszy trailer gry Dead Island zrobił wielką...             143   
49919  O ujawnienie jego treści od dawna walczą organ...             109   
49920  75 min. - na boisku walka w środku pola, a żół...              77   

       New Char Count     id  label_pred  \
0                 705      0          17   
1                 618      1          26   
2                 404      3          24   
3                1409      4          37   
4                 566      8          25   
...               ...    ...         ...   
49916             707  99838          23   
49917             660  99839          36   
49918            1033  99841          12   
49919             850  99845          28   
49920             478  99846          19   

                                                    text  label_gold  diff  
0      Godne polecenia ( choć paliwożerne ) są turbod...          17     0  
1      Natalia Partyka też przegrała 3:4 , tyle że z ...          30     4  
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...          24     0  
3      Opiekowała się rodzinami oficerów , którzy zgi...          37  

In [21]:
df = merged_df.copy()
tokenizer = AutoTokenizer.from_pretrained("hyperonym/xlm-roberta-longformer-base-16384")  # USE SAME TOKENIZER AS USED IN TRAINING
def check_split_position(row):
    text = row['Modified text']
    words = text.split()
    cumulative_tokens = 0
    for i in range(row['Split Location']):  # Assuming Split Location is 1-based index
        tokens = tokenizer.tokenize(words[i])
        cumulative_tokens += len(tokens)
        if cumulative_tokens > 2048:  # Check if we've already passed 2048 tokens
            return "Outside"
    return "Inside"
df['Token Limit Check'] = df.apply(check_split_position, axis=1)
df

ISO             LLM used     Type Data Split  \
0      POL               GPT-o1  Partial       Test   
1      POL               GPT-o1  Partial       Test   
2      POL     Gemini-Flash-1.5  Partial       Test   
3      POL               GPT-o1  Partial       Test   
4      POL    Claude-Sonnet-3.5  Partial       Test   
...    ...                  ...      ...        ...   
49916  POL  Amazon-Nova-Pro-1.0  Partial       Test   
49917  POL     Claude-Haiku-3.5  Partial       Test   
49918  POL               Aya-23  Partial       Test   
49919  POL               Aya-23  Partial       Test   
49920  POL     Claude-Haiku-3.5  Partial       Test   

                                           Original text  Original Word Count  \
0      Godne polecenia (choć paliwożerne) są turbodoł...                   41   
1      Natalia Partyka też przegrała 3:4, tyle że z K...                   52   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...                   43   
3      Opiekowała się rodzinami oficerów, którzy zgin...                   49   
4      W minionym tygodniu gminne dożynki odbyły się ...                   46   
...                                                  ...                  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...                   43   
49917  Film - który wywołał oburzenie krytyków w Cann...                   63   
49918  Pierwszy trailer gry Dead Island zrobił wielką...                   33   
49919  O ujawnienie jego treści od dawna walczą organ...                   56   
49920  75 min. - na boisku walka w środku pola, a żół...                   32   

       Original Char Count  Split Location  \
0                      344              17   
1                      317              30   
2                      297              24   
3                      376              37   
4                      325              25   
...                    ...             ...   
49916                  311              26   
49917                  449              36   
49918                  250              17   
49919                  393              28   
49920                  192              19   

                                           Modified text  New Word Count  \
0      Godne polecenia ( choć paliwożerne ) są turbod...              95   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...              95   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...              58   
3      Opiekowała się rodzinami oficerów , którzy zgi...             211   
4      W minionym tygodniu gminne dożynki odbyły się ...              76   
...                                                  ...             ...   
49916  Efektownymi porównaniami rzucali też szefowie ...              91   
49917  Film - który wywołał oburzenie krytyków w Cann...              94   
49918  Pierwszy trailer gry Dead Island zrobił wielką...             143   
49919  O ujawnienie jego treści od dawna walczą organ...             109   
49920  75 min. - na boisku walka w środku pola, a żół...              77   

       New Char Count     id  label_pred  \
0                 705      0          17   
1                 618      1          26   
2                 404      3          24   
3                1409      4          37   
4                 566      8          25   
...               ...    ...         ...   
49916             707  99838          23   
49917             660  99839          36   
49918            1033  99841          12   
49919             850  99845          28   
49920             478  99846          19   

                                                    text  label_gold  diff  \
0      Godne polecenia ( choć paliwożerne ) są turbod...          17     0   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...          30     4   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...          24     0   
3      Opiekowała się rodzinami oficerów , którzy zgi...          

In [22]:
df['Token Limit Check'].value_counts()

Token Limit Check
Inside    49921
Name: count, dtype: int64

In [23]:
df['Split Location'].max()

375

In [24]:
# prompt: 2 new columns in df_demo as series/list of zeroes and ones : WORDS_REAL : length is row's Word Count, start with row's Split Location number of zeroes and end with ones : WORDS_PRED : lenght is rows' Word Count , start with row's label_pred number of zeroes and end wit ones
def create_word_series(row, column_name):
  word_count = row['New Word Count']
  split_location = row[column_name]
  series = [0] * split_location + [1] * (word_count - split_location)
  return series
df['WORDS_REAL'] = df.apply(create_word_series, axis=1, args=('Split Location',))
df['WORDS_PRED'] = df.apply(create_word_series, axis=1, args=('label_pred',))
df

ISO             LLM used     Type Data Split  \
0      POL               GPT-o1  Partial       Test   
1      POL               GPT-o1  Partial       Test   
2      POL     Gemini-Flash-1.5  Partial       Test   
3      POL               GPT-o1  Partial       Test   
4      POL    Claude-Sonnet-3.5  Partial       Test   
...    ...                  ...      ...        ...   
49916  POL  Amazon-Nova-Pro-1.0  Partial       Test   
49917  POL     Claude-Haiku-3.5  Partial       Test   
49918  POL               Aya-23  Partial       Test   
49919  POL               Aya-23  Partial       Test   
49920  POL     Claude-Haiku-3.5  Partial       Test   

                                           Original text  Original Word Count  \
0      Godne polecenia (choć paliwożerne) są turbodoł...                   41   
1      Natalia Partyka też przegrała 3:4, tyle że z K...                   52   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...                   43   
3      Opiekowała się rodzinami oficerów, którzy zgin...                   49   
4      W minionym tygodniu gminne dożynki odbyły się ...                   46   
...                                                  ...                  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...                   43   
49917  Film - który wywołał oburzenie krytyków w Cann...                   63   
49918  Pierwszy trailer gry Dead Island zrobił wielką...                   33   
49919  O ujawnienie jego treści od dawna walczą organ...                   56   
49920  75 min. - na boisku walka w środku pola, a żół...                   32   

       Original Char Count  Split Location  \
0                      344              17   
1                      317              30   
2                      297              24   
3                      376              37   
4                      325              25   
...                    ...             ...   
49916                  311              26   
49917                  449              36   
49918                  250              17   
49919                  393              28   
49920                  192              19   

                                           Modified text  New Word Count  \
0      Godne polecenia ( choć paliwożerne ) są turbod...              95   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...              95   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...              58   
3      Opiekowała się rodzinami oficerów , którzy zgi...             211   
4      W minionym tygodniu gminne dożynki odbyły się ...              76   
...                                                  ...             ...   
49916  Efektownymi porównaniami rzucali też szefowie ...              91   
49917  Film - który wywołał oburzenie krytyków w Cann...              94   
49918  Pierwszy trailer gry Dead Island zrobił wielką...             143   
49919  O ujawnienie jego treści od dawna walczą organ...             109   
49920  75 min. - na boisku walka w środku pola, a żół...              77   

       New Char Count     id  label_pred  \
0                 705      0          17   
1                 618      1          26   
2                 404      3          24   
3                1409      4          37   
4                 566      8          25   
...               ...    ...         ...   
49916             707  99838          23   
49917             660  99839          36   
49918            1033  99841          12   
49919             850  99845          28   
49920             478  99846          19   

                                                    text  label_gold  diff  \
0      Godne polecenia ( choć paliwożerne ) są turbod...          17     0   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...          30     4   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...          24     0   
3      Opiekowała się rodzinami oficerów , którzy zgi...          

In [25]:
# prompt: 4 new columns : ROW_TP, ROW_FP, ROW_TN , ROW_FN : based on zeroes and ones in WORDS_PRED , WORDS_REAL . note : lenght of series is diff in each row
def calculate_metrics(row):
  tp = 0
  fp = 0
  tn = 0
  fn = 0
  for i in range(len(row['WORDS_REAL'])):
    if row['WORDS_REAL'][i] == 1 and row['WORDS_PRED'][i] == 1:
      tp += 1
    elif row['WORDS_REAL'][i] == 0 and row['WORDS_PRED'][i] == 1:
      fp += 1
    elif row['WORDS_REAL'][i] == 0 and row['WORDS_PRED'][i] == 0:
      tn += 1
    elif row['WORDS_REAL'][i] == 1 and row['WORDS_PRED'][i] == 0:
      fn += 1
  return tp, fp, tn, fn
df[['ROW_TP', 'ROW_FP', 'ROW_TN', 'ROW_FN']] = df.apply(calculate_metrics, axis=1, result_type='expand')
df

ISO             LLM used     Type Data Split  \
0      POL               GPT-o1  Partial       Test   
1      POL               GPT-o1  Partial       Test   
2      POL     Gemini-Flash-1.5  Partial       Test   
3      POL               GPT-o1  Partial       Test   
4      POL    Claude-Sonnet-3.5  Partial       Test   
...    ...                  ...      ...        ...   
49916  POL  Amazon-Nova-Pro-1.0  Partial       Test   
49917  POL     Claude-Haiku-3.5  Partial       Test   
49918  POL               Aya-23  Partial       Test   
49919  POL               Aya-23  Partial       Test   
49920  POL     Claude-Haiku-3.5  Partial       Test   

                                           Original text  Original Word Count  \
0      Godne polecenia (choć paliwożerne) są turbodoł...                   41   
1      Natalia Partyka też przegrała 3:4, tyle że z K...                   52   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...                   43   
3      Opiekowała się rodzinami oficerów, którzy zgin...                   49   
4      W minionym tygodniu gminne dożynki odbyły się ...                   46   
...                                                  ...                  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...                   43   
49917  Film - który wywołał oburzenie krytyków w Cann...                   63   
49918  Pierwszy trailer gry Dead Island zrobił wielką...                   33   
49919  O ujawnienie jego treści od dawna walczą organ...                   56   
49920  75 min. - na boisku walka w środku pola, a żół...                   32   

       Original Char Count  Split Location  \
0                      344              17   
1                      317              30   
2                      297              24   
3                      376              37   
4                      325              25   
...                    ...             ...   
49916                  311              26   
49917                  449              36   
49918                  250              17   
49919                  393              28   
49920                  192              19   

                                           Modified text  New Word Count  ...  \
0      Godne polecenia ( choć paliwożerne ) są turbod...              95  ...   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...              95  ...   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...              58  ...   
3      Opiekowała się rodzinami oficerów , którzy zgi...             211  ...   
4      W minionym tygodniu gminne dożynki odbyły się ...              76  ...   
...                                                  ...             ...  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...              91  ...   
49917  Film - który wywołał oburzenie krytyków w Cann...              94  ...   
49918  Pierwszy trailer gry Dead Island zrobił wielką...             143  ...   
49919  O ujawnienie jego treści od dawna walczą organ...             109  ...   
49920  75 min. - na boisku walka w środku pola, a żół...              77  ...   

                                                    text  label_gold  diff  \
0      Godne polecenia ( choć paliwożerne ) są turbod...          17     0   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...          30     4   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...          24     0   
3      Opiekowała się rodzinami oficerów , którzy zgi...          37     0   
4      W minionym tygodniu gminne dożynki odbyły się ...          25     0   
...                                                  ...         ...   ...   
49916  Efektownymi porównaniami rzucali też szefowie ...          26     3   
49917  Film - który wywołał oburzenie krytyków w Cann...          36     0   
49918  Pierwszy trailer gry Dead Island zrobił wielką...          17     5   
49919  O ujawnienie jego treści od dawna walczą organ...          2

In [26]:
# prompt: 4 new column : ROW_ACC , ROW_PREC , ROW_REC , ROW_F1 based on ROW_TN,ROW_TP,ROW_FN,ROW_FP
def calculate_row_metrics(row):
  tp = row['ROW_TP']
  fp = row['ROW_FP']
  tn = row['ROW_TN']
  fn = row['ROW_FN']
  if (tp + tn + fp + fn) == 0:
    accuracy = 0
  else:
    accuracy = (tp + tn) / (tp + tn + fp + fn)
  if (tp + fp) == 0:
    precision = 0
  else:
    precision = tp / (tp + fp)
  if (tp + fn) == 0:
    recall = 0
  else:
    recall = tp / (tp + fn)
  if (precision + recall) == 0:
    f1_score = 0
  else:
    f1_score = 2 * (precision * recall) / (precision + recall)
  return accuracy, precision, recall, f1_score
df[['ROW_ACC', 'ROW_PREC', 'ROW_REC', 'ROW_F1']] = df.apply(calculate_row_metrics, axis=1, result_type='expand')
df

ISO             LLM used     Type Data Split  \
0      POL               GPT-o1  Partial       Test   
1      POL               GPT-o1  Partial       Test   
2      POL     Gemini-Flash-1.5  Partial       Test   
3      POL               GPT-o1  Partial       Test   
4      POL    Claude-Sonnet-3.5  Partial       Test   
...    ...                  ...      ...        ...   
49916  POL  Amazon-Nova-Pro-1.0  Partial       Test   
49917  POL     Claude-Haiku-3.5  Partial       Test   
49918  POL               Aya-23  Partial       Test   
49919  POL               Aya-23  Partial       Test   
49920  POL     Claude-Haiku-3.5  Partial       Test   

                                           Original text  Original Word Count  \
0      Godne polecenia (choć paliwożerne) są turbodoł...                   41   
1      Natalia Partyka też przegrała 3:4, tyle że z K...                   52   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...                   43   
3      Opiekowała się rodzinami oficerów, którzy zgin...                   49   
4      W minionym tygodniu gminne dożynki odbyły się ...                   46   
...                                                  ...                  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...                   43   
49917  Film - który wywołał oburzenie krytyków w Cann...                   63   
49918  Pierwszy trailer gry Dead Island zrobił wielką...                   33   
49919  O ujawnienie jego treści od dawna walczą organ...                   56   
49920  75 min. - na boisku walka w środku pola, a żół...                   32   

       Original Char Count  Split Location  \
0                      344              17   
1                      317              30   
2                      297              24   
3                      376              37   
4                      325              25   
...                    ...             ...   
49916                  311              26   
49917                  449              36   
49918                  250              17   
49919                  393              28   
49920                  192              19   

                                           Modified text  New Word Count  ...  \
0      Godne polecenia ( choć paliwożerne ) są turbod...              95  ...   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...              95  ...   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...              58  ...   
3      Opiekowała się rodzinami oficerów , którzy zgi...             211  ...   
4      W minionym tygodniu gminne dożynki odbyły się ...              76  ...   
...                                                  ...             ...  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...              91  ...   
49917  Film - który wywołał oburzenie krytyków w Cann...              94  ...   
49918  Pierwszy trailer gry Dead Island zrobił wielką...             143  ...   
49919  O ujawnienie jego treści od dawna walczą organ...             109  ...   
49920  75 min. - na boisku walka w środku pola, a żół...              77  ...   

                                              WORDS_REAL  \
0      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
4      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
...                                                  ...   
49916  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
49917  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
49918  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
49919  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
49920  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                              WORDS_PRED  ROW_TP ROW_FP  \
0      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

In [27]:
def calculate_percentage_of_ones(row):
  series = row['WORDS_PRED']
  if len(series) == 0:
    return 0
  else:
    return sum(series) / len(series)
df["Label : 1"] = df.apply(calculate_percentage_of_ones, axis=1)
df["Label : 0"] = 1.0 - df["Label : 1"]
df

ISO             LLM used     Type Data Split  \
0      POL               GPT-o1  Partial       Test   
1      POL               GPT-o1  Partial       Test   
2      POL     Gemini-Flash-1.5  Partial       Test   
3      POL               GPT-o1  Partial       Test   
4      POL    Claude-Sonnet-3.5  Partial       Test   
...    ...                  ...      ...        ...   
49916  POL  Amazon-Nova-Pro-1.0  Partial       Test   
49917  POL     Claude-Haiku-3.5  Partial       Test   
49918  POL               Aya-23  Partial       Test   
49919  POL               Aya-23  Partial       Test   
49920  POL     Claude-Haiku-3.5  Partial       Test   

                                           Original text  Original Word Count  \
0      Godne polecenia (choć paliwożerne) są turbodoł...                   41   
1      Natalia Partyka też przegrała 3:4, tyle że z K...                   52   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...                   43   
3      Opiekowała się rodzinami oficerów, którzy zgin...                   49   
4      W minionym tygodniu gminne dożynki odbyły się ...                   46   
...                                                  ...                  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...                   43   
49917  Film - który wywołał oburzenie krytyków w Cann...                   63   
49918  Pierwszy trailer gry Dead Island zrobił wielką...                   33   
49919  O ujawnienie jego treści od dawna walczą organ...                   56   
49920  75 min. - na boisku walka w środku pola, a żół...                   32   

       Original Char Count  Split Location  \
0                      344              17   
1                      317              30   
2                      297              24   
3                      376              37   
4                      325              25   
...                    ...             ...   
49916                  311              26   
49917                  449              36   
49918                  250              17   
49919                  393              28   
49920                  192              19   

                                           Modified text  New Word Count  ...  \
0      Godne polecenia ( choć paliwożerne ) są turbod...              95  ...   
1      Natalia Partyka też przegrała 3:4 , tyle że z ...              95  ...   
2      Niemcy chcieli wybudować trzy takie wjazdy, uk...              58  ...   
3      Opiekowała się rodzinami oficerów , którzy zgi...             211  ...   
4      W minionym tygodniu gminne dożynki odbyły się ...              76  ...   
...                                                  ...             ...  ...   
49916  Efektownymi porównaniami rzucali też szefowie ...              91  ...   
49917  Film - który wywołał oburzenie krytyków w Cann...              94  ...   
49918  Pierwszy trailer gry Dead Island zrobił wielką...             143  ...   
49919  O ujawnienie jego treści od dawna walczą organ...             109  ...   
49920  75 min. - na boisku walka w środku pola, a żół...              77  ...   

       ROW_TP  ROW_FP  ROW_TN ROW_FN   ROW_ACC  ROW_PREC ROW_REC    ROW_F1  \
0          78       0      17      0  1.000000  1.000000     1.0  1.000000   
1          65       4      26      0  0.957895  0.942029     1.0  0.970149   
2          34       0      24      0  1.000000  1.000000     1.0  1.000000   
3         174       0      37      0  1.000000  1.000000     1.0  1.000000   
4          51       0      25      0  1.000000  1.000000     1.0  1.000000   
...       ...     ...     ...    ...       ...       ...     ...       ...   
49916      65       3      23      0  0.967033  0.955882     1.0  0.977444   
49917      58       0      36      0  1.000000  1.000000     1.0  1.000000   
49918     126       5      12      0  0.965035  0.961832     1.0  0.980545   
49919      81       0      28      0  1.000000  1.000000     1.0  1

In [28]:
df_unchanged = df[df['Type'] == 'Unchanged']
df_rewritten = df[df['Type'] == 'Rewritten']
df_partial   = df[df['Type'] == 'Partial']
print("######################################")
print(" METRICS BY TEXT TYPE : ")
print("######################################")
AVG_ACC  = df_partial['ROW_ACC'].mean()
AVG_PREC = df_partial['ROW_PREC'].mean()
AVG_REC  = df_partial['ROW_REC'].mean()
AVG_F1   = df_partial['ROW_F1'].mean()
print("Partial Cases : Average Accuracy : "  , AVG_ACC )
print("Partial Cases : Average Precision : " , AVG_PREC)
print("Partial Cases : Average Recall : "    , AVG_REC )
print("Partial Cases : Average F1-score : "  , AVG_F1  )
AVG_ACC  = df_unchanged['ROW_ACC'].mean()
AVG_PREC = df_unchanged['ROW_PREC'].mean()
AVG_REC  = df_unchanged['ROW_REC'].mean()
AVG_F1   = df_unchanged['ROW_F1'].mean()
print("Unchanged Cases : Average Accuracy : "  , AVG_ACC )
print("Unchanged Cases : Average Precision : " , AVG_PREC)
print("Unchanged Cases : Average Recall : "    , AVG_REC )
print("Unchanged Cases : Average F1-score : "  , AVG_F1  )
AVG_ACC  = df_rewritten['ROW_ACC'].mean()
AVG_PREC = df_rewritten['ROW_PREC'].mean()
AVG_REC  = df_rewritten['ROW_REC'].mean()
AVG_F1   = df_rewritten['ROW_F1'].mean()
print("Rewritten Cases : Average Accuracy : "  , AVG_ACC )
print("Rewritten Cases : Average Precision : " , AVG_PREC)
print("Rewritten Cases : Average Recall : "    , AVG_REC )
print("Rewritten Cases : Average F1-score : "  , AVG_F1  )
print("######################################")
print(" METRICS OVERALL : ")
print("######################################")
# prompt: print AVG_ACC, AVG_PREC , AVG_REC , AVG_F1 as mean of values in columns ROW_ACC , ROW_REC , ROW_PREC , ROW_F1 from dataframe df
AVG_ACC = df['ROW_ACC'].mean()
AVG_PREC = df['ROW_PREC'].mean()
AVG_REC = df['ROW_REC'].mean()
AVG_F1 = df['ROW_F1'].mean()
print("All Cases : Average Accuracy:", AVG_ACC)
print("All Cases : Average Precision:", AVG_PREC)
print("All Cases : Average Recall:", AVG_REC)
print("All Cases : Average F1-score:", AVG_F1)
print("######################################")
# prompt: Also print overall ACC,PREC,REC,F1 based on values of columns ROW_TN,ROW_TP,ROW_FN,ROW_FP
total_tp = df['ROW_TP'].sum()
total_fp = df['ROW_FP'].sum()
total_tn = df['ROW_TN'].sum()
total_fn = df['ROW_FN'].sum()
if (total_tp + total_tn + total_fp + total_fn) == 0:
  accuracy = 0
else:
  accuracy = (total_tp + total_tn) / (total_tp + total_tn + total_fp + total_fn)
if (total_tp + total_fp) == 0:
  precision = 0
else:
  precision = total_tp / (total_tp + total_fp)
if (total_tp + total_fn) == 0:
  recall = 0
else:
  recall = total_tp / (total_tp + total_fn)
if (precision + recall) == 0:
  f1_score = 0
else:
  f1_score = 2 * (precision * recall) / (precision + recall)
print("Overall Accuracy:", accuracy)
print("Overall Precision:", precision)
print("Overall Recall:", recall)
print("Overall F1-score:", f1_score)

######################################
 METRICS BY TEXT TYPE : 
######################################
Partial Cases : Average Accuracy :  0.9570058330170521
Partial Cases : Average Precision :  0.9530425145666854
Partial Cases : Average Recall :  0.9900518439649512
Partial Cases : Average F1-score :  0.9656579960470106
Unchanged Cases : Average Accuracy :  0.5657269341134558
Unchanged Cases : Average Precision :  0.0
Unchanged Cases : Average Recall :  0.0
Unchanged Cases : Average F1-score :  0.0
Rewritten Cases : Average Accuracy :  0.9735035828125072
Rewritten Cases : Average Precision :  1.0
Rewritten Cases : Average Recall :  0.9735035828125072
Rewritten Cases : Average F1-score :  0.9808400644941
######################################
 METRICS OVERALL : 
######################################
All Cases : Average Accuracy: 0.9190410063254509
All Cases : Average Precision: 0.8612414527780528
All Cases : Average Recall: 0.8882211449444186
All Cases : Average F1-score: 0.86943586952

In [29]:
llm_values = df['LLM used'].unique()
for llm in llm_values:
    print("LLM used:", llm)
    df_llm = df[df['LLM used'] == llm]
    for text_type in ['Partial', 'Unchanged', 'Rewritten']:
        df_subset = df_llm[df_llm['Type'] == text_type]
        if df_subset.empty:
            continue
        avg_acc  = df_subset['ROW_ACC'].mean()
        avg_prec = df_subset['ROW_PREC'].mean()
        avg_rec  = df_subset['ROW_REC'].mean()
        avg_f1   = df_subset['ROW_F1'].mean()
        print(f"{text_type} Cases : Average Accuracy : {avg_acc}")
        print(f"{text_type} Cases : Average Precision : {avg_prec}")
        print(f"{text_type} Cases : Average Recall : {avg_rec}")
        print(f"{text_type} Cases : Average F1-score : {avg_f1}")
    print("######################################")

LLM used: GPT-o1
Partial Cases : Average Accuracy : 0.9900886943011742
Partial Cases : Average Precision : 0.9898292924387625
Partial Cases : Average Recall : 0.9966696073322895
Partial Cases : Average F1-score : 0.9931007127418364
Unchanged Cases : Average Accuracy : 0.5877615582528447
Unchanged Cases : Average Precision : 0.0
Unchanged Cases : Average Recall : 0.0
Unchanged Cases : Average F1-score : 0.0
Rewritten Cases : Average Accuracy : 0.9655167815663577
Rewritten Cases : Average Precision : 1.0
Rewritten Cases : Average Recall : 0.9655167815663577
Rewritten Cases : Average F1-score : 0.9778338017296966
######################################
LLM used: Gemini-Flash-1.5
Partial Cases : Average Accuracy : 0.9858661554067739
Partial Cases : Average Precision : 0.982400864909452
Partial Cases : Average Recall : 0.9993504463411779
Partial Cases : Average F1-score : 0.9888783303226257
Unchanged Cases : Average Accuracy : 0.58729546556291
Unchanged Cases : Average Precision : 0.0
Unchan

In [30]:
llm_values = df['LLM used'].unique()
for llm in llm_values:
    print("LLM used:", llm)
    df_llm = df[df['LLM used'] == llm]
    total_tp = df_llm['ROW_TP'].sum()
    total_fp = df_llm['ROW_FP'].sum()
    total_tn = df_llm['ROW_TN'].sum()
    total_fn = df_llm['ROW_FN'].sum()
    if (total_tp + total_tn + total_fp + total_fn) == 0:
        accuracy = 0
    else:
        accuracy = (total_tp + total_tn) / (total_tp + total_tn + total_fp + total_fn)
    if (total_tp + total_fp) == 0:
        precision = 0
    else:
        precision = total_tp / (total_tp + total_fp)
    if (total_tp + total_fn) == 0:
        recall = 0
    else:
        recall = total_tp / (total_tp + total_fn)
    if (precision + recall) == 0:
        f1_score = 0
    else:
        f1_score = 2 * (precision * recall) / (precision + recall)
    print("Overall Accuracy:", accuracy)
    print("Overall Precision:", precision)
    print("Overall Recall:", recall)
    print("Overall F1-score:", f1_score)
    print("######################################")

LLM used: GPT-o1
Overall Accuracy: 0.9669718498054718
Overall Precision: 0.9596984745165602
Overall Recall: 0.9941733011710889
Overall F1-score: 0.9766317446324714
######################################
LLM used: Gemini-Flash-1.5
Overall Accuracy: 0.9531919109899564
Overall Precision: 0.9346170627616204
Overall Recall: 0.9993147963888311
Overall F1-score: 0.9658837309660316
######################################
LLM used: Claude-Sonnet-3.5
Overall Accuracy: 0.957599125765389
Overall Precision: 0.9406776647941406
Overall Recall: 0.9983924588963815
Overall F1-score: 0.9686761456519868
######################################
LLM used: Mistral-Large-2411
Overall Accuracy: 0.9195711681285528
Overall Precision: 0.8918671292480497
Overall Recall: 0.9927288864613915
Overall F1-score: 0.9395989959754204
######################################
LLM used: Aya-23
Overall Accuracy: 0.8645300875261012
Overall Precision: 0.8568488707170984
Overall Recall: 0.9601292957708382
Overall F1-score: 0.905553757

In [31]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 49921 entries, 0 to 49920
Data columns (total 29 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   ISO                  49921 non-null  object 
 1   LLM used             49921 non-null  object 
 2   Type                 49921 non-null  object 
 3   Data Split           49921 non-null  object 
 4   Original text        49921 non-null  object 
 5   Original Word Count  49921 non-null  int64  
 6   Original Char Count  49921 non-null  int64  
 7   Split Location       49921 non-null  int64  
 8   Modified text        49921 non-null  object 
 9   New Word Count       49921 non-null  int64  
 10  New Char Count       49921 non-null  int64  
 11  id                   49921 non-null  int64  
 12  label_pred           49921 non-null  int64  
 13  text                 49921 non-null  object 
 14  label_gold           49921 non-null  int64  
 15  diff                 49921 non-null 

In [32]:
df.to_csv("POL-INFERENCE-4.csv")

In [33]:
print("CLICK CTRL+S, WAIT 2 SEC FOR IT TO BE SAVED, DOWNLOAD BOTH CODE AND THE CSV FILE FROM RUNTIME")

CLICK CTRL+S, WAIT 2 SEC FOR IT TO BE SAVED, DOWNLOAD BOTH CODE AND THE CSV FILE FROM RUNTIME
